In [1]:
import numpy as np
import os, sys
sys.path.append('../')
from src.datasets.soccernet_generic_wcombined import soccernet_dataset_generic
from src.utils.helper import samples_by_language
import src.utils.training_helper as training_helper
import torch
from torch.utils.data import Dataset, DataLoader

/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torchaudio/backend/utils.py:54: UserWarning: "sox" backend is being deprecated. The default backend will be changed to "sox_io" backend in 0.8.0 and "sox" backend will be removed in 0.9.0. Please migrate to "sox_io" backend. Please refer to https://github.com/pytorch/audio/issues/903 for the detail.
  '"sox" backend is being deprecated. '


In [2]:
root_dir = "/work/oarongve/data/sound_dataset/SoccerNet-code/data/"
train_list = "/work/oarongve/data/sound_dataset/SoccerNet-code/data/listgame_Train_300.npy"
valid_list = "/work/oarongve/data/sound_dataset/SoccerNet-code/data/listgame_Valid_100.npy"
test_list = "/work/oarongve/data/sound_dataset/SoccerNet-code/data/listgame_Test_100.npy"


In [3]:
# Disable warnings
import warnings
warnings.filterwarnings('ignore')

In [4]:
%%bash
nvidia-smi

Fri Mar  5 22:49:55 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 450.102.04   Driver Version: 450.102.04   CUDA Version: 11.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM3...  On   | 00000000:E0:00.0 Off |                    0 |
| N/A   27C    P0    47W / 350W |      0MiB / 32510MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  Tesla V100-SXM3...  On   | 00000000:E2:00.0 Off |                    0 |
| N/A   

In [5]:
langpath_train = '/work/oarongve/project-daredevil/project-daredevil/language-annotations/annotations/train_lang_dict.json'
langpath_valid = '/work/oarongve/project-daredevil/project-daredevil/language-annotations/annotations/valid_lang_dict.json'
langpath_test = '/work/oarongve/project-daredevil/project-daredevil/language-annotations/annotations/test_lang_dict.json'

samples_train_all = samples_by_language(langpath_train,train_list,'all')
samples_valid_all = samples_by_language(langpath_valid,valid_list,'all')
samples_test_all = samples_by_language(langpath_test,test_list,'all')


In [6]:
test_set_all = soccernet_dataset_generic(npy_file=test_list,root_dir=root_dir,lang='all',lang_dict=langpath_test)
test_set_all.load_waves()
test_set_all.generate_mel_spectrograms(load_features=True)
test_set_all.load_resnet_features()
test_set_all.load_combined()

100%|██████████| 100/100 [00:01<00:00, 55.77it/s]


In [7]:
valid_set_all = soccernet_dataset_generic(npy_file=valid_list,root_dir=root_dir,lang='all',lang_dict=langpath_valid)


In [8]:
params = {'batch_size': 32,
         'shuffle': True,
         'num_workers':4}

# window size

w = 8

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [9]:
valid_set_all = soccernet_dataset_generic(npy_file=valid_list,root_dir=root_dir,lang='all',lang_dict=langpath_valid)

valid_set_all.load_waves()
valid_set_all.generate_mel_spectrograms(load_features=True)
valid_set_all.load_resnet_features()
valid_set_all.load_combined()

100%|██████████| 100/100 [00:01<00:00, 56.80it/s]


In [10]:
validloader_all = DataLoader(valid_set_all,**params)
testloader_all = DataLoader(valid_set_all,**params)


# Case 1 : Train on combined features

## Window size

In [11]:
import torchvision
import torch.optim as optim
import torch.nn as nn
def generate_model():
    model = torchvision.models.resnet18(pretrained=True)
    model.conv1 = nn.Conv2d(1,64,kernel_size=(7,7),stride=(2,2),padding=(3,3),bias=False)
    model.fc = nn.Linear(512,4,bias=True)
    #resnet.features.conv0 = nn.Conv2d(1, 96, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    #resnet.classifier = nn.Linear(in_features=densenet.classifier.in_features, out_features=3,bias=True)


    criterion = nn.CrossEntropyLoss()
    optimizer = optim.SGD(model.parameters(), lr=0.001, momentum=0.9)
    return model, criterion,optimizer

In [12]:
windows = [2,4,8,16,32]

# Case 2: Visual

In [13]:
import torchvision
import torch.optim as optim
import torch.nn as nn
import torch.nn.functional as F


class Net(nn.Module):
    def __init__(self,feature_size,window_size_seconds,T_field_seconds):
        super(Net, self).__init__()
        
        T = window_size_seconds*2
        T_field = T_field_seconds*2
        fc1_size = (32)*(T-(T_field-1))
        
        self.conv1 = nn.Conv2d(1,out_channels=32,kernel_size=(1,feature_size))
        self.bn1 = nn.BatchNorm2d(self.conv1.out_channels)
        self.conv2 = nn.Conv2d(1,out_channels=32,kernel_size=(T_field,32))
        self.bn2 = nn.BatchNorm2d(self.conv2.out_channels)
        self.fc1 = nn.Linear(fc1_size, 240)
        self.fc2 = nn.Linear(self.fc1.out_features, 240)
        self.fc3 = nn.Linear(240, 4)

    def forward(self, x):
        
                
        x = F.relu(self.bn1(self.conv1(x)))
        x = x.permute(0,3,2,1)
        x = F.relu(self.bn2(self.conv2(x)))
        x = x.reshape(x.size(0),-1)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x

## Window size

In [14]:
def evaluate_model(model,dataloader,feature_name,device):
    #if not feature_name == 'combined_spot' or not feature_name == 'resnet_spot':
    #    return "Bad feature name!"
    running_loss=0.0
    model.to(device)
    best_acc = 0
    with torch.no_grad():
        model.eval()
        res = torch.zeros((4,4))
        for i, data in enumerate(dataloader, 0):
            # get the inputs; data is a list of [inputs, labels]
            inputs = data[feature_name].unsqueeze(1).to(device)
            label = data['label'].to(device)

            # forward + backward + optimize
            outputs = model(inputs)

            preds = torch.argmax(outputs,dim=1)

            for p,gt in zip(preds,label):
                res[int(p),int(gt)] += 1




        N_total = res.sum()
        N_correct = res.diag().sum()

        acc = N_correct / N_total
        print(f"Accuracy : {acc}")
    
    return acc

In [15]:
import torch.nn as nn
import torch.nn.functional as F

class Net(nn.Module):
    def __init__(self,feature_size,window_size_seconds,T_field_seconds):
        super(Net, self).__init__()
        
        T = window_size_seconds*2
        T_field = T_field_seconds*2
        fc1_size = (32)*(T-(T_field-1))
        
        self.conv1 = nn.Conv2d(1,out_channels=32,kernel_size=(1,feature_size))
        self.bn1 = nn.BatchNorm2d(self.conv1.out_channels)
        self.conv2 = nn.Conv2d(1,out_channels=32,kernel_size=(T_field,32))
        self.bn2 = nn.BatchNorm2d(self.conv2.out_channels)
        self.fc1 = nn.Linear(fc1_size, 240)
        self.fc2 = nn.Linear(self.fc1.out_features, 240)
        self.fc3 = nn.Linear(240, 4)

    def forward(self, x):
        
                
        x = F.relu(self.bn1(self.conv1(x)))
        x = x.permute(0,3,2,1)
        x = F.relu(self.bn2(self.conv2(x)))
        x = x.reshape(x.size(0),-1)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x

# Case 3 B) Softmax average

In [24]:
def evaluate_softmax_fusion(dataloader,visual_model,audio_model):
    visual_model.to(device)
    audio_model.to(device)
    visual_model.eval()
    audio_model.eval()
    
    with torch.no_grad():
        res_audio = torch.zeros((4,4))
        res_visual = torch.zeros((4,4))
        res_average = torch.zeros((4,4))
        res_smax = torch.zeros((4,4))
        res_lmax = torch.zeros((4,4))
        
        all_labels = list()
        all_preds = list()
        all_preds_raw = list()
        
        for i, data in enumerate(dataloader, 0):
            # get the inputs; data is a list of [inputs, labels]
            inputs_audio = data['ms_spot'].unsqueeze(1).to(device)
            inputs_visual = data['resnet_spot'].unsqueeze(1).to(device)
            label = data['label'].to(device)

            # forward + backward + optimize
            outputs_audio = audio_model(inputs_audio)
            outputs_visual = visual_model(inputs_visual)
            
            softmax_audio = torch.softmax(outputs_audio,dim=1) # MAKE SURE DIMS ARE CORRECT, TEST
            softmax_visual = torch.softmax(outputs_visual,dim=1)
            softmax_average = (softmax_audio + softmax_visual) / 2

            logit_max = torch.max(outputs_audio,outputs_visual)
            softmax_max = torch.max(softmax_audio,softmax_visual)
            
            
            preds_audio = torch.argmax(outputs_audio,dim=1)
            preds_visual = torch.argmax(outputs_visual,dim=1)
            preds_average = torch.argmax(softmax_average,dim=1)
            preds_smax = torch.argmax(softmax_max,dim=1)
            preds_lmax = torch.argmax(logit_max,dim=1)
            
            all_preds_raw.append((softmax_audio,softmax_visual,softmax_average))
            all_preds.append((preds_audio,preds_visual,preds_average,preds_smax,preds_lmax))
            all_labels.append(label)

            for p,gt in zip(preds_audio,label):
                res_audio[int(p),int(gt)] += 1
            
            for p,gt in zip(preds_visual,label):
                res_visual[int(p),int(gt)] += 1

            for p,gt in zip(preds_average,label):
                res_average[int(p),int(gt)] += 1
                
            for p,gt in zip(preds_smax,label):
                res_smax[int(p),int(gt)] += 1
                
            for p,gt in zip(preds_lmax,label):
                res_lmax[int(p),int(gt)] += 1
                
                
        # Audio
        N_total_audio = res_audio.sum()
        N_correct_audio = res_audio.diag().sum()
        acc_audio = N_correct_audio / N_total_audio
        
        N_total_visual = res_visual.sum()
        N_correct_visual = res_visual.diag().sum()
        acc_visual = N_correct_visual / N_total_visual
        
        N_total_average = res_average.sum()
        N_correct_average = res_average.diag().sum()
        acc_average = N_correct_average / N_total_average
        
        N_total_smax = res_smax.sum()
        N_correct_smax = res_smax.diag().sum()
        acc_smax = N_correct_smax / N_total_smax
        
        N_total_lmax = res_lmax.sum()
        N_correct_lmax = res_lmax.diag().sum()
        acc_lmax = N_correct_lmax / N_total_lmax
        
        print(f"Audio Accuracy : {acc_audio},\
              Visual Accuracy : {acc_visual},\
              Average Accuracy : {acc_average},\
              smax Accuracy : {acc_smax},\
              lmax Accuracy : {acc_lmax}")
        
    return acc_audio, # 0
            acc_visual, # 1
            acc_average, # 2
            acc_smax, # 3
            acc_lmax, # 4
            (res_audio,res_visual,res_average,res_smax), # 5
            (all_preds,all_labels,all_preds_raw) #6


IndentationError: unexpected indent (<ipython-input-24-6b7edc205540>, line 90)

In [23]:
def evaluate_softmax_fusion(dataloader,visual_model,audio_model):
    visual_model.to(device)
    audio_model.to(device)
    visual_model.eval()
    audio_model.eval()
    
    with torch.no_grad():
        res_audio = torch.zeros((4,4))
        res_visual = torch.zeros((4,4))
        res_average = torch.zeros((4,4))
        res_smax = torch.zeros((4,4))
        res_lmax = torch.zeros((4,4))
        
        all_labels = list()
        all_preds = list()
        all_preds_raw = list()
        
        for i, data in enumerate(dataloader, 0):
            # get the inputs; data is a list of [inputs, labels]
            inputs_audio = data['ms_spot'].unsqueeze(1).to(device)
            inputs_visual = data['resnet_spot'].unsqueeze(1).to(device)
            label = data['label'].to(device)

            # forward + backward + optimize
            outputs_audio = audio_model(inputs_audio)
            outputs_visual = visual_model(inputs_visual)
            
            softmax_audio = torch.softmax(outputs_audio,dim=1) # MAKE SURE DIMS ARE CORRECT, TEST
            softmax_visual = torch.softmax(outputs_visual,dim=1)
            softmax_average = (softmax_audio + softmax_visual) / 2

            logit_max = torch.max(outputs_audio,outputs_visual)
            softmax_max = torch.max(softmax_audio,softmax_visual)
            
            
            preds_audio = torch.argmax(outputs_audio,dim=1)
            preds_visual = torch.argmax(outputs_visual,dim=1)
            preds_average = torch.argmax(softmax_average,dim=1)
            preds_smax = torch.argmax(softmax_max,dim=1)
            preds_lmax = torch.argmax(logit_max,dim=1)
            
            all_preds_raw.append((softmax_audio,softmax_visual,softmax_average))
            all_preds.append((preds_audio,preds_visual,preds_average,preds_smax,preds_lmax))
            all_labels.append(label)

            for p,gt in zip(preds_audio,label):
                res_audio[int(p),int(gt)] += 1
            
            for p,gt in zip(preds_visual,label):
                res_visual[int(p),int(gt)] += 1

            for p,gt in zip(preds_average,label):
                res_average[int(p),int(gt)] += 1
                
            for p,gt in zip(preds_smax,label):
                res_smax[int(p),int(gt)] += 1
                
            for p,gt in zip(preds_lmax,label):
                res_lmax[int(p),int(gt)] += 1
                
                
        # Audio
        N_total_audio = res_audio.sum()
        N_correct_audio = res_audio.diag().sum()
        acc_audio = N_correct_audio / N_total_audio
        
        N_total_visual = res_visual.sum()
        N_correct_visual = res_visual.diag().sum()
        acc_visual = N_correct_visual / N_total_visual
        
        N_total_average = res_average.sum()
        N_correct_average = res_average.diag().sum()
        acc_average = N_correct_average / N_total_average
        
        N_total_smax = res_smax.sum()
        N_correct_smax = res_smax.diag().sum()
        acc_smax = N_correct_smax / N_total_smax
        
        N_total_lmax = res_lmax.sum()
        N_correct_lmax = res_lmax.diag().sum()
        acc_lmax = N_correct_lmax / N_total_lmax
        
        print(f"Audio Accuracy : {acc_audio},\
              Visual Accuracy : {acc_visual},\
              Average Accuracy : {acc_average},\
              smax Accuracy : {acc_smax},\
              lmax Accuracy : {acc_lmax}")
        
    return acc_audio, acc_visual, acc_average, acc_smax, acc_lmax, (res_audio,res_visual,res_average,res_smax), (all_preds,all_labels,all_preds_raw) #6


In [22]:
avg_w_accs_valid = list()
avg_w_accs_test = list()

for w in windows:
    print(w)
    valid_set_all.set_window_size(w)
    test_set_all.set_window_size(w)
    
    validloader = DataLoader(valid_set_all,**params)
    testloader = DataLoader(test_set_all,**params)
    
    # generate models
    visual_model = Net(512,w,w//2)
    audio_model, _,_ = generate_model()
    
    # load models
    visual_model.load_state_dict(torch.load("./weights/best_model_visual_"+str(w)+".pth"))
    audio_model.load_state_dict(torch.load("./weights/best_model_audio_"+str(w)+".pth"))
    
    avg_w_accs_valid.append(evaluate_softmax_fusion(validloader,visual_model,audio_model))
    avg_w_accs_test.append(evaluate_softmax_fusion(testloader,visual_model,audio_model))
    

2
Audio Accuracy : 0.6353846192359924,              Visual Accuracy : 0.810769259929657,              Average Accuracy : 0.7871794700622559,              smax Accuracy : 0.7846153974533081,              lmax Accuracy : 0.7543589472770691
Audio Accuracy : 0.6111387610435486,              Visual Accuracy : 0.7981103658676147,              Average Accuracy : 0.7692690491676331,              smax Accuracy : 0.7608155012130737,              lmax Accuracy : 0.7284932732582092
4
Audio Accuracy : 0.6825640797615051,              Visual Accuracy : 0.8425641059875488,              Average Accuracy : 0.8230769038200378,              smax Accuracy : 0.8230769038200378,              lmax Accuracy : 0.8112820386886597
Audio Accuracy : 0.6727995872497559,              Visual Accuracy : 0.8438587784767151,              Average Accuracy : 0.8239681720733643,              smax Accuracy : 0.8184982538223267,              lmax Accuracy : 0.8204873204231262
8
Audio Accuracy : 0.7215384840965271,           

In [23]:
import sklearn.metrics

In [24]:
a = 3
p_type = 2

In [25]:
def generate_c_report(l,w):
    labels = torch.cat(l[w][6][1]).cpu()
    
    reports = list()
    
    for pred_type in range(len(l[w][6][0][0])):
        current_preds = list()

        for p in l[w][6][0]:

            current_preds.append(p[pred_type].cpu())

        preds = torch.cat(current_preds)
        r = sklearn.metrics.classification_report(y_pred = preds,y_true=labels,output_dict=True)
        reports.append(r)
        
    return reports

In [60]:
windows = {w:i for i,w in enumerate([2,4,8,16,32])}

In [101]:
avg_w_accs_valid[4][6][0][0][5]

IndexError: tuple index out of range

In [292]:
avg_w_accs_valid[4][6][0][2][1] == 

tensor([False,  True,  True, False, False, False, False, False,  True, False,
         True, False, False, False,  True,  True,  True, False,  True, False,
        False, False,  True, False, False, False, False, False,  True, False,
        False,  True], device='cuda:0')

In [94]:
avg_w_accs_valid[2][6][1]

[tensor([2, 0, 3, 2, 1, 2, 1, 2, 0, 3, 3, 3, 0, 1, 1, 2, 0, 3, 1, 1, 1, 2, 3, 3,
         0, 1, 3, 3, 0, 0, 3, 0], device='cuda:0'),
 tensor([1, 0, 1, 0, 0, 0, 2, 3, 2, 2, 0, 2, 0, 2, 0, 1, 1, 0, 1, 0, 3, 3, 3, 1,
         1, 3, 2, 0, 0, 3, 2, 1], device='cuda:0'),
 tensor([2, 2, 0, 0, 1, 0, 3, 0, 2, 0, 3, 3, 3, 0, 2, 3, 1, 3, 0, 3, 0, 3, 1, 2,
         3, 0, 3, 3, 3, 3, 1, 2], device='cuda:0'),
 tensor([1, 3, 2, 1, 3, 2, 2, 3, 0, 0, 1, 1, 1, 1, 0, 3, 3, 0, 0, 0, 0, 2, 1, 3,
         1, 0, 0, 3, 1, 0, 0, 0], device='cuda:0'),
 tensor([3, 0, 3, 3, 0, 3, 3, 0, 1, 2, 3, 2, 1, 1, 0, 0, 2, 2, 1, 2, 1, 0, 3, 2,
         0, 0, 3, 3, 1, 0, 1, 3], device='cuda:0'),
 tensor([3, 2, 1, 1, 1, 3, 1, 1, 1, 0, 3, 2, 1, 3, 3, 0, 3, 1, 3, 0, 3, 1, 1, 3,
         3, 0, 2, 3, 1, 3, 3, 2], device='cuda:0'),
 tensor([0, 3, 2, 3, 1, 2, 2, 1, 2, 0, 0, 1, 1, 3, 2, 3, 3, 1, 2, 3, 0, 3, 3, 3,
         0, 0, 1, 1, 3, 3, 1, 3], device='cuda:0'),
 tensor([3, 1, 1, 0, 1, 1, 1, 2, 2, 0, 0, 1, 3, 0, 1, 0, 1, 3, 0, 0, 

In [65]:
windows[32]

4

In [71]:
reports_test = dict()
for w in [2,4,8,16,32]:
    reports_test[w] = generate_c_report(avg_w_accs_test,windows[w])


In [68]:
reports_valid = dict()
for w in [2,4,8,16,32]:
    reports_valid[w] = generate_c_report(avg_w_accs_valid,windows[w])


In [74]:
reports_test[8]

[{'0': {'precision': 0.6496674057649667,
   'recall': 0.6467991169977925,
   'f1-score': 0.6482300884955752,
   'support': 453},
  '1': {'precision': 0.6944908180300501,
   'recall': 0.7184801381692574,
   'f1-score': 0.7062818336162988,
   'support': 579},
  '2': {'precision': 0.9423076923076923,
   'recall': 0.901840490797546,
   'f1-score': 0.9216300940438872,
   'support': 326},
  '3': {'precision': 0.6579352850539292,
   'recall': 0.6539050535987749,
   'f1-score': 0.6559139784946236,
   'support': 653},
  'accuracy': 0.7110890104425659,
  'macro avg': {'precision': 0.7361003002891595,
   'recall': 0.7302561998908428,
   'f1-score': 0.7330139986625962,
   'support': 2011},
  'weighted avg': {'precision': 0.7126969504144468,
   'recall': 0.7110890104425659,
   'f1-score': 0.711759647124629,
   'support': 2011}},
 {'0': {'precision': 0.8687782805429864,
   'recall': 0.847682119205298,
   'f1-score': 0.8581005586592179,
   'support': 453},
  '1': {'precision': 0.9092526690391459,
   

In [33]:
import pandas as pd


In [34]:
print(pd.DataFrame(reports[8][0]).T.round(3).to_latex())

KeyError: 8

In [40]:
print(pd.DataFrame(reports[8][1]).T.round(3).to_latex())

KeyError: 8

In [227]:
p_type = 2

In [256]:
avg_w_accs_valid[0][6][1][0]

tensor([0, 2, 2, 3, 2, 2, 3, 1, 2, 3, 3, 2, 0, 1, 0, 1, 3, 2, 1, 3, 1, 1, 1, 0,
        3, 0, 0, 1, 3, 0, 0, 1], device='cuda:0')

In [253]:
len(avg_w_accs_valid[0][6][1][0])

32

In [ ]:
avg_w_accs_valid[<windowsize>]
                [<6> -> get tuple of (preds,labels,raw)]
                [0 for preds, 1 for labels]
                [for labels, a batch, for preds (preds_audio,preds_visual,preds_average,preds_smax,preds_lmax)]

In [25]:
def get_classwise_info(res,window_size,prediction_type):
    
    # Convert windows to correct index
    windows = {w:i for i,w in enumerate([2,4,8,16,32])}
    
    # Convert type to correct index
    p_type = {
        'audio': 0,
        'visual': 1,
        'avg': 2,
        'smax': 3,
        'lmax': 4
    }
    
    # Get correct idx
    wsize_idx = windows[window_size]
    pred_idx = p_type[prediction_type]
    
    # predictoins
    y_p = list()
    for e in res[wsize_idx][6][0]:
        y_p.append(e[pred_idx])
    y_p = torch.cat(y_p)
    y_p = y_p.cpu()
    
    #labels
    y_t = torch.cat(res[wsize_idx][6][1]).cpu()
    print(sklearn.metrics.classification_report(digits=3,target_names=['Card','Substitutuion','Goal','Background'],
                                                y_true=y_t,
                                                y_pred=y_p))

In [229]:
# Chosen window size
wc = windows[32]

In [264]:
y_p = list()
for e in avg_w_accs_valid[wc][6][0]:
    y_p.append(e[2])
y_p = torch.cat(y_p)
y_p = y_p.cpu()

In [265]:
l = torch.cat(avg_w_accs_valid[wc][6][1]).cpu()

In [284]:
print(sklearn.metrics.classification_report(digits=3,target_names=['Card','Substitutuion','Goal','Background'],y_true=l,y_pred=y_p))

               precision    recall  f1-score   support

         Card      0.876     0.889     0.882       396
Substitutuion      0.939     0.956     0.947       562
         Goal      0.943     0.969     0.956       356
   Background      0.920     0.882     0.900       636

     accuracy                          0.921      1950
    macro avg      0.919     0.924     0.921      1950
 weighted avg      0.920     0.921     0.920      1950



In [296]:
get_classwise_info(avg_w_accs_test,16,'audio')

               precision    recall  f1-score   support

         Card      0.672     0.704     0.688       453
Substitutuion      0.777     0.674     0.722       579
         Goal      0.908     0.874     0.891       326
   Background      0.646     0.712     0.677       653

     accuracy                          0.726      2011
    macro avg      0.750     0.741     0.744      2011
 weighted avg      0.732     0.726     0.727      2011



# Results per class

## Results audio

In [314]:
get_classwise_info(avg_w_accs_test,2,'audio')

               precision    recall  f1-score   support

         Card      0.564     0.552     0.558       453
Substitutuion      0.625     0.573     0.598       579
         Goal      0.851     0.825     0.838       326
   Background      0.524     0.579     0.550       653

     accuracy                          0.611      2011
    macro avg      0.641     0.632     0.636      2011
 weighted avg      0.615     0.611     0.612      2011



In [316]:
get_classwise_info(avg_w_accs_test,4,'audio')

               precision    recall  f1-score   support

         Card      0.601     0.618     0.609       453
Substitutuion      0.651     0.672     0.661       579
         Goal      0.919     0.902     0.910       326
   Background      0.622     0.597     0.609       653

     accuracy                          0.673      2011
    macro avg      0.698     0.697     0.697      2011
 weighted avg      0.674     0.673     0.673      2011



In [317]:
get_classwise_info(avg_w_accs_test,8,'audio')

               precision    recall  f1-score   support

         Card      0.650     0.647     0.648       453
Substitutuion      0.694     0.718     0.706       579
         Goal      0.942     0.902     0.922       326
   Background      0.658     0.654     0.656       653

     accuracy                          0.711      2011
    macro avg      0.736     0.730     0.733      2011
 weighted avg      0.713     0.711     0.712      2011



In [318]:
get_classwise_info(avg_w_accs_test,16,'audio')

               precision    recall  f1-score   support

         Card      0.672     0.704     0.688       453
Substitutuion      0.777     0.674     0.722       579
         Goal      0.908     0.874     0.891       326
   Background      0.646     0.712     0.677       653

     accuracy                          0.726      2011
    macro avg      0.750     0.741     0.744      2011
 weighted avg      0.732     0.726     0.727      2011



In [319]:
get_classwise_info(avg_w_accs_test,32,'audio')

               precision    recall  f1-score   support

         Card      0.632     0.664     0.648       453
Substitutuion      0.817     0.770     0.793       579
         Goal      0.867     0.837     0.852       326
   Background      0.691     0.714     0.702       653

     accuracy                          0.739      2011
    macro avg      0.752     0.746     0.749      2011
 weighted avg      0.743     0.739     0.740      2011



# Results visual

In [320]:
get_classwise_info(avg_w_accs_test,2,'visual')

               precision    recall  f1-score   support

         Card      0.811     0.757     0.783       453
Substitutuion      0.866     0.794     0.829       579
         Goal      0.803     0.936     0.864       326
   Background      0.734     0.761     0.747       653

     accuracy                          0.798      2011
    macro avg      0.803     0.812     0.806      2011
 weighted avg      0.801     0.798     0.798      2011



In [321]:
get_classwise_info(avg_w_accs_test,4,'visual')

               precision    recall  f1-score   support

         Card      0.836     0.808     0.822       453
Substitutuion      0.885     0.874     0.879       579
         Goal      0.885     0.923     0.904       326
   Background      0.793     0.802     0.798       653

     accuracy                          0.844      2011
    macro avg      0.850     0.852     0.851      2011
 weighted avg      0.844     0.844     0.844      2011



In [322]:
get_classwise_info(avg_w_accs_test,8,'visual')

               precision    recall  f1-score   support

         Card      0.869     0.848     0.858       453
Substitutuion      0.909     0.883     0.896       579
         Goal      0.898     0.942     0.919       326
   Background      0.830     0.845     0.838       653

     accuracy                          0.872      2011
    macro avg      0.876     0.879     0.878      2011
 weighted avg      0.873     0.872     0.872      2011



In [323]:
get_classwise_info(avg_w_accs_test,16,'visual')

               precision    recall  f1-score   support

         Card      0.873     0.850     0.861       453
Substitutuion      0.923     0.869     0.895       579
         Goal      0.941     0.923     0.932       326
   Background      0.820     0.885     0.851       653

     accuracy                          0.879      2011
    macro avg      0.889     0.882     0.885      2011
 weighted avg      0.881     0.879     0.879      2011



In [324]:
get_classwise_info(avg_w_accs_test,32,'visual')

               precision    recall  f1-score   support

         Card      0.873     0.892     0.882       453
Substitutuion      0.933     0.870     0.901       579
         Goal      0.959     0.942     0.950       326
   Background      0.842     0.887     0.864       653

     accuracy                          0.892      2011
    macro avg      0.902     0.898     0.899      2011
 weighted avg      0.894     0.892     0.893      2011



## results avg

In [325]:
get_classwise_info(avg_w_accs_test,2,'avg')

               precision    recall  f1-score   support

         Card      0.776     0.751     0.763       453
Substitutuion      0.803     0.741     0.771       579
         Goal      0.878     0.929     0.903       326
   Background      0.684     0.727     0.705       653

     accuracy                          0.769      2011
    macro avg      0.786     0.787     0.786      2011
 weighted avg      0.771     0.769     0.769      2011



In [326]:
get_classwise_info(avg_w_accs_test,4,'avg')

               precision    recall  f1-score   support

         Card      0.796     0.790     0.793       453
Substitutuion      0.818     0.841     0.830       579
         Goal      0.937     0.951     0.944       326
   Background      0.791     0.769     0.780       653

     accuracy                          0.824      2011
    macro avg      0.835     0.838     0.836      2011
 weighted avg      0.823     0.824     0.824      2011



In [327]:
get_classwise_info(avg_w_accs_test,8,'avg')

               precision    recall  f1-score   support

         Card      0.865     0.832     0.848       453
Substitutuion      0.857     0.872     0.865       579
         Goal      0.940     0.957     0.948       326
   Background      0.818     0.819     0.819       653

     accuracy                          0.860      2011
    macro avg      0.870     0.870     0.870      2011
 weighted avg      0.860     0.860     0.860      2011



In [328]:
get_classwise_info(avg_w_accs_test,16,'avg')

               precision    recall  f1-score   support

         Card      0.870     0.874     0.872       453
Substitutuion      0.922     0.893     0.907       579
         Goal      0.969     0.948     0.958       326
   Background      0.846     0.876     0.861       653

     accuracy                          0.892      2011
    macro avg      0.902     0.898     0.900      2011
 weighted avg      0.893     0.892     0.892      2011



In [329]:
get_classwise_info(avg_w_accs_test,32,'avg')

               precision    recall  f1-score   support

         Card      0.867     0.892     0.879       453
Substitutuion      0.945     0.914     0.929       579
         Goal      0.960     0.948     0.954       326
   Background      0.882     0.896     0.889       653

     accuracy                          0.909      2011
    macro avg      0.913     0.912     0.913      2011
 weighted avg      0.909     0.909     0.909      2011



## More results if needed

# Results per class end

In [29]:
avg_w_accs_valid[a][5][1]

tensor([[346.,  16.,   5.,  27.],
        [ 16., 517.,   0.,  38.],
        [  0.,   0., 334.,  18.],
        [ 34.,  29.,  17., 553.]])

In [30]:
avg_w_accs_valid[a][5][2]

tensor([[343.,  11.,   5.,  48.],
        [ 16., 515.,   0.,  36.],
        [  5.,   1., 344.,  11.],
        [ 32.,  35.,   7., 541.]])

In [31]:
avg_w_accs_test[a][5][3]

tensor([[396.,  15.,   4.,  49.],
        [ 11., 518.,   2.,  33.],
        [  1.,   2., 310.,   7.],
        [ 45.,  44.,  10., 564.]])

In [51]:
X = torch.rand(3,3)

In [52]:
X[1]

tensor([0.0653, 0.4062, 0.9920])

In [35]:
for e in avg_w_accs_valid:
    print(e)

(tensor(0.6354), tensor(0.8108), tensor(0.7872), tensor(0.7846), tensor(0.7544), (tensor([[210.,  61.,  25.,  96.],
        [ 56., 336.,   8., 120.],
        [ 28.,  10., 294.,  21.],
        [102., 155.,  29., 399.]]), tensor([[308.,  29.,   0.,  47.],
        [ 28., 472.,   0.,  58.],
        [  1.,   6., 331.,  61.],
        [ 59.,  55.,  25., 470.]]), tensor([[305.,  30.,   5.,  61.],
        [ 28., 439.,   2.,  80.],
        [  9.,   3., 327.,  31.],
        [ 54.,  90.,  22., 464.]]), tensor([[303.,  28.,   5.,  64.],
        [ 30., 444.,   3.,  87.],
        [ 11.,   3., 331.,  33.],
        [ 52.,  87.,  17., 452.]])), ([(tensor([0, 1, 1, 1, 1, 0, 0, 0, 0, 3, 2, 0, 1, 1, 1, 1, 0, 2, 1, 2, 2, 0, 1, 2,
        3, 3, 0, 2, 3, 3, 2, 0], device='cuda:0'), tensor([3, 1, 1, 0, 1, 0, 0, 3, 0, 3, 2, 1, 1, 1, 1, 0, 3, 0, 2, 2, 2, 0, 1, 2,
        1, 3, 3, 2, 1, 3, 2, 0], device='cuda:0'), tensor([0, 1, 1, 0, 1, 0, 0, 0, 0, 3, 2, 1, 1, 1, 1, 0, 3, 0, 1, 2, 2, 0, 1, 2,
        1, 3, 0, 2, 

(tensor(0.6826), tensor(0.8426), tensor(0.8231), tensor(0.8231), tensor(0.8113), (tensor([[245.,  45.,  15., 111.],
        [ 49., 361.,   3., 114.],
        [  8.,   6., 320.,   6.],
        [ 94., 150.,  18., 405.]]), tensor([[326.,  22.,   2.,  46.],
        [ 28., 495.,   0.,  52.],
        [  0.,   2., 326.,  42.],
        [ 42.,  43.,  28., 496.]]), tensor([[319.,  17.,   5.,  64.],
        [ 22., 473.,   1.,  83.],
        [  4.,   4., 336.,  12.],
        [ 51.,  68.,  14., 477.]]), tensor([[320.,  16.,   5.,  64.],
        [ 21., 476.,   1.,  86.],
        [  5.,   4., 337.,  14.],
        [ 50.,  66.,  13., 472.]])), ([(tensor([1, 3, 2, 3, 0, 0, 1, 1, 0, 1, 0, 2, 1, 0, 2, 3, 3, 0, 1, 1, 1, 2, 3, 1,
        1, 3, 3, 0, 3, 1, 0, 3], device='cuda:0'), tensor([1, 2, 2, 0, 0, 3, 1, 1, 2, 1, 0, 2, 3, 3, 2, 3, 3, 1, 1, 1, 1, 2, 3, 1,
        1, 0, 3, 0, 1, 1, 0, 3], device='cuda:0'), tensor([1, 3, 2, 3, 0, 0, 1, 1, 2, 1, 0, 2, 1, 3, 2, 3, 3, 0, 1, 1, 1, 2, 3, 1,
        1, 3, 3, 0, 

(tensor(0.7215), tensor(0.8708), tensor(0.8621), tensor(0.8579), tensor(0.8585), (tensor([[250.,  47.,  12.,  93.],
        [ 54., 393.,   4.,  94.],
        [  8.,   2., 324.,   9.],
        [ 84., 120.,  16., 440.]]), tensor([[339.,  20.,   2.,  37.],
        [ 18., 497.,   0.,  47.],
        [  0.,   4., 339.,  29.],
        [ 39.,  41.,  15., 523.]]), tensor([[327.,  14.,   4.,  43.],
        [ 27., 490.,   1.,  61.],
        [  3.,   0., 347.,  15.],
        [ 39.,  58.,   4., 517.]]), tensor([[327.,  14.,   4.,  46.],
        [ 28., 490.,   1.,  65.],
        [  4.,   0., 347.,  16.],
        [ 37.,  58.,   4., 509.]])), ([(tensor([1, 0, 3, 2, 3, 0, 2, 0, 2, 1, 1, 3, 3, 3, 1, 3, 0, 3, 3, 1, 2, 3, 3, 1,
        1, 3, 1, 1, 2, 3, 0, 1], device='cuda:0'), tensor([1, 2, 1, 2, 3, 0, 2, 0, 2, 1, 1, 1, 3, 1, 0, 3, 0, 3, 3, 1, 2, 3, 3, 1,
        1, 3, 3, 3, 2, 3, 0, 3], device='cuda:0'), tensor([1, 0, 1, 2, 3, 0, 2, 0, 2, 1, 1, 1, 3, 3, 1, 3, 0, 3, 3, 1, 2, 3, 3, 1,
        1, 3, 1, 3, 

(tensor(0.7390), tensor(0.8974), tensor(0.8938), tensor(0.8903), tensor(0.8892), (tensor([[264.,  34.,  18., 106.],
        [ 31., 406.,   1.,  64.],
        [ 10.,   4., 317.,  12.],
        [ 91., 118.,  20., 454.]]), tensor([[346.,  16.,   5.,  27.],
        [ 16., 517.,   0.,  38.],
        [  0.,   0., 334.,  18.],
        [ 34.,  29.,  17., 553.]]), tensor([[343.,  11.,   5.,  48.],
        [ 16., 515.,   0.,  36.],
        [  5.,   1., 344.,  11.],
        [ 32.,  35.,   7., 541.]]), tensor([[341.,  11.,   6.,  49.],
        [ 15., 516.,   0.,  38.],
        [  5.,   1., 342.,  12.],
        [ 35.,  34.,   8., 537.]])), ([(tensor([0, 2, 0, 1, 0, 1, 1, 1, 0, 0, 0, 1, 3, 1, 1, 2, 1, 3, 2, 2, 0, 0, 2, 0,
        0, 3, 1, 1, 3, 0, 0, 3], device='cuda:0'), tensor([0, 2, 3, 1, 0, 1, 3, 1, 0, 3, 0, 1, 3, 1, 1, 2, 1, 3, 2, 2, 3, 3, 2, 3,
        0, 3, 1, 1, 3, 0, 0, 3], device='cuda:0'), tensor([0, 2, 3, 1, 0, 1, 1, 1, 0, 0, 0, 1, 3, 1, 1, 2, 1, 3, 2, 2, 3, 3, 2, 0,
        0, 3, 1, 1, 

(tensor(0.7549), tensor(0.9067), tensor(0.9205), tensor(0.9159), tensor(0.9108), (tensor([[256.,  35.,  18.,  93.],
        [ 35., 446.,   5.,  61.],
        [ 27.,   6., 311.,  23.],
        [ 78.,  75.,  22., 459.]]), tensor([[359.,  15.,   9.,  37.],
        [ 11., 508.,   1.,  27.],
        [  2.,   0., 336.,   7.],
        [ 24.,  39.,  10., 565.]]), tensor([[352.,   6.,   2.,  42.],
        [ 10., 537.,   0.,  25.],
        [ 11.,   2., 345.,   8.],
        [ 23.,  17.,   9., 561.]]), tensor([[348.,   6.,   4.,  42.],
        [ 10., 537.,   0.,  25.],
        [ 12.,   2., 343.,  11.],
        [ 26.,  17.,   9., 558.]])), ([(tensor([1, 3, 1, 2, 0, 2, 2, 0, 1, 2, 2, 0, 2, 2, 3, 2, 1, 2, 3, 2, 0, 1, 1, 1,
        0, 3, 1, 1, 1, 1, 1, 2], device='cuda:0'), tensor([1, 3, 1, 0, 3, 2, 2, 0, 1, 2, 2, 2, 2, 2, 3, 2, 2, 2, 1, 2, 3, 1, 1, 1,
        0, 3, 1, 1, 3, 3, 1, 2], device='cuda:0'), tensor([1, 3, 1, 2, 3, 2, 2, 0, 1, 2, 2, 2, 2, 2, 3, 2, 2, 2, 1, 2, 3, 1, 1, 1,
        0, 3, 1, 1, 

In [36]:
for wsize,tacc in zip(windows,avg_w_accs_test):
    print(wsize,tacc)

2 (tensor(0.6111), tensor(0.7981), tensor(0.7693), tensor(0.7608), tensor(0.7285), (tensor([[250.,  65.,  16., 112.],
        [ 46., 332.,  11., 142.],
        [ 17.,   9., 269.,  21.],
        [140., 173.,  30., 378.]]), tensor([[343.,  26.,   5.,  49.],
        [ 26., 460.,   1.,  44.],
        [  2.,  10., 305.,  63.],
        [ 82.,  83.,  15., 497.]]), tensor([[340.,  31.,   3.,  64.],
        [ 22., 429.,   3.,  80.],
        [  6.,   2., 303.,  34.],
        [ 85., 117.,  17., 475.]]), tensor([[344.,  36.,   4.,  72.],
        [ 25., 429.,   4.,  92.],
        [  7.,   5., 302.,  34.],
        [ 77., 109.,  16., 455.]])), ([(tensor([2, 3, 2, 1, 3, 0, 2, 0, 3, 1, 0, 2, 2, 2, 0, 1, 1, 0, 2, 3, 1, 0, 3, 3,
        0, 0, 1, 0, 2, 2, 2, 3], device='cuda:0'), tensor([0, 3, 2, 3, 3, 3, 2, 0, 2, 3, 3, 2, 2, 2, 0, 1, 3, 2, 2, 1, 1, 0, 1, 3,
        1, 0, 3, 0, 2, 2, 2, 3], device='cuda:0'), tensor([2, 3, 2, 1, 3, 0, 2, 0, 3, 1, 3, 2, 2, 2, 0, 1, 1, 0, 2, 1, 1, 0, 3, 3,
        1, 0, 1, 0

4 (tensor(0.6728), tensor(0.8439), tensor(0.8240), tensor(0.8185), tensor(0.8205), (tensor([[280.,  63.,   9., 114.],
        [ 64., 389.,   7., 138.],
        [  8.,   7., 294.,  11.],
        [101., 120.,  16., 390.]]), tensor([[366.,  18.,   2.,  52.],
        [ 20., 506.,   0.,  46.],
        [  2.,   6., 301.,  31.],
        [ 65.,  49.,  23., 524.]]), tensor([[358.,  28.,   3.,  61.],
        [ 32., 487.,   4.,  72.],
        [  1.,   2., 310.,  18.],
        [ 62.,  62.,   9., 502.]]), tensor([[357.,  30.,   4.,  61.],
        [ 32., 484.,   4.,  78.],
        [  1.,   3., 310.,  19.],
        [ 63.,  62.,   8., 495.]])), ([(tensor([2, 1, 3, 0, 3, 3, 1, 3, 3, 2, 1, 3, 1, 1, 0, 3, 2, 1, 3, 1, 3, 2, 3, 1,
        0, 1, 2, 3, 0, 3, 3, 1], device='cuda:0'), tensor([2, 3, 3, 3, 3, 3, 3, 1, 3, 2, 1, 3, 3, 1, 0, 3, 1, 1, 3, 3, 3, 3, 3, 1,
        0, 3, 2, 3, 2, 3, 3, 0], device='cuda:0'), tensor([2, 3, 3, 3, 3, 3, 3, 1, 3, 2, 1, 3, 3, 1, 0, 3, 1, 1, 3, 3, 3, 2, 3, 1,
        0, 3, 2, 3

8 (tensor(0.7111), tensor(0.8722), tensor(0.8598), tensor(0.8583), tensor(0.8548), (tensor([[293.,  45.,  14.,  99.],
        [ 58., 416.,   7., 118.],
        [  4.,   5., 294.,   9.],
        [ 98., 113.,  11., 427.]]), tensor([[384.,  16.,   5.,  37.],
        [ 14., 511.,   0.,  37.],
        [  5.,   3., 307.,  27.],
        [ 50.,  49.,  14., 552.]]), tensor([[377.,  13.,   6.,  40.],
        [ 21., 505.,   2.,  61.],
        [  1.,   2., 312.,  17.],
        [ 54.,  59.,   6., 535.]]), tensor([[376.,  14.,   7.,  45.],
        [ 22., 507.,   2.,  61.],
        [  1.,   2., 313.,  17.],
        [ 54.,  56.,   4., 530.]])), ([(tensor([3, 3, 0, 2, 3, 3, 1, 1, 2, 3, 1, 0, 3, 2, 3, 3, 3, 3, 1, 0, 1, 3, 2, 2,
        1, 3, 1, 3, 1, 1, 2, 1], device='cuda:0'), tensor([2, 1, 1, 3, 3, 3, 3, 1, 2, 3, 3, 0, 1, 2, 3, 3, 1, 3, 1, 3, 1, 3, 2, 2,
        1, 3, 1, 2, 1, 1, 2, 1], device='cuda:0'), tensor([3, 1, 1, 3, 3, 3, 3, 1, 2, 3, 3, 0, 1, 2, 3, 3, 1, 3, 1, 3, 1, 3, 2, 2,
        1, 3, 1, 3

16 (tensor(0.7255), tensor(0.8787), tensor(0.8921), tensor(0.8891), tensor(0.8851), (tensor([[319.,  50.,  14.,  92.],
        [ 27., 390.,   5.,  80.],
        [  5.,   8., 285.,  16.],
        [102., 131.,  22., 465.]]), tensor([[385.,  15.,   6.,  35.],
        [ 17., 503.,   0.,  25.],
        [  2.,   2., 301.,  15.],
        [ 49.,  59.,  19., 578.]]), tensor([[396.,  12.,   4.,  43.],
        [ 11., 517.,   2.,  31.],
        [  1.,   2., 309.,   7.],
        [ 45.,  48.,  11., 572.]]), tensor([[396.,  15.,   4.,  49.],
        [ 11., 518.,   2.,  33.],
        [  1.,   2., 310.,   7.],
        [ 45.,  44.,  10., 564.]])), ([(tensor([0, 2, 1, 1, 3, 1, 0, 1, 2, 1, 2, 1, 2, 1, 3, 0, 0, 0, 1, 0, 1, 3, 3, 3,
        1, 0, 1, 3, 0, 2, 2, 1], device='cuda:0'), tensor([3, 3, 3, 3, 3, 1, 3, 1, 2, 1, 2, 1, 2, 1, 2, 0, 0, 1, 1, 0, 1, 1, 1, 1,
        1, 1, 1, 3, 0, 2, 2, 3], device='cuda:0'), tensor([0, 3, 3, 3, 3, 1, 0, 1, 2, 1, 2, 1, 2, 1, 2, 0, 0, 1, 1, 0, 1, 1, 1, 1,
        1, 1, 1, 

32 (tensor(0.7389), tensor(0.8921), tensor(0.9085), tensor(0.9065), tensor(0.9015), (tensor([[301.,  44.,  27., 104.],
        [ 29., 446.,   6.,  65.],
        [ 17.,   7., 273.,  18.],
        [106.,  82.,  20., 466.]]), tensor([[404.,  15.,   2.,  42.],
        [ 11., 504.,   1.,  24.],
        [  3.,   2., 307.,   8.],
        [ 35.,  58.,  16., 579.]]), tensor([[404.,  16.,   3.,  43.],
        [  8., 529.,   1.,  22.],
        [  8.,   2., 309.,   3.],
        [ 33.,  32.,  13., 585.]]), tensor([[402.,  16.,   3.,  42.],
        [  9., 529.,   1.,  25.],
        [  8.,   2., 310.,   4.],
        [ 34.,  32.,  12., 582.]])), ([(tensor([2, 0, 3, 2, 0, 3, 0, 0, 1, 3, 3, 1, 0, 1, 3, 2, 2, 3, 2, 3, 3, 3, 1, 0,
        3, 3, 0, 0, 2, 3, 2, 1], device='cuda:0'), tensor([2, 0, 3, 2, 3, 3, 0, 0, 1, 0, 3, 1, 0, 3, 3, 2, 2, 1, 2, 2, 3, 1, 3, 2,
        3, 3, 1, 1, 2, 1, 2, 1], device='cuda:0'), tensor([2, 0, 3, 2, 3, 3, 0, 0, 1, 0, 3, 1, 0, 1, 3, 2, 2, 3, 2, 3, 3, 1, 3, 2,
        3, 3, 1, 

## Window size

## Window slide

In [ ]:
avg_pos_accs_valid = list()
avg_pos_accs_test = list()

for pos in window_pos:
    print(w)
    valid_set_all.set_window_pos(pos)
    test_set_all.set_window_pos(pos)
    
    train_set_all.set_window_size(best_w)
    valid_set_all.set_window_size(best_w)
    test_set_all.set_window_size(best_w)
    
    validloader = DataLoader(valid_set_all,**params)
    testloader = DataLoader(test_set_all,**params)
    
    # generate models
    visual_model = Net(512,w,w//2)
    audio_model = model, _,_ = generate_model()
    
    # load models
    visual_model.load_state_dict(torch.load("./weights/best_model_visual_slide_"+str(pos)+".pth"))
    audio_model.load_state_dict(torch.load("./weights/best_model_audio_slide_"+str(pos)+".pth"))
    
    avg_pos_accs_valid.append(evaluate_softmax_fusion(validloader,visual_model,audio_model))
    avg_pos_accs_test.append(evaluate_softmax_fusion(testloader,visual_model,audio_model))
    

## Language

# Video

In [26]:
import torchvision.transforms._transforms_video as video_transform
import torchvision.transforms as transforms
import src.datasets.utils.custom_transforms as custom_transforms

mean = [0.43216, 0.394666, 0.37645]
std = [0.22803, 0.22145, 0.216989]

newsize=(112,112)

transform_train_list = [video_transform.ToTensorVideo()]
transform_train_list.append(custom_transforms.ReSize(newsize))
transform_train_list.append(video_transform.RandomHorizontalFlipVideo(0.5))
transform_train_list.append(video_transform.NormalizeVideo(std,mean,inplace=True))

transform_valid_list = [video_transform.ToTensorVideo()]
transform_valid_list.append(custom_transforms.ReSize(newsize))
transform_valid_list.append(video_transform.NormalizeVideo(std,mean,inplace=True))



In [27]:


transform_train = transforms.Compose(transform_train_list)
transform_valid = transforms.Compose(transform_valid_list)

In [28]:
from src.datasets.soccernet_generic_wvideo import soccernet_dataset_generic as vid_set

In [ ]:
vid_train_set = vid_set(npy_file=train_list,root_dir=root_dir,lang='all',transform=transform_train,lang_dict=langpath_train)
vid_train_set.load_waves()
vid_train_set.generate_mel_spectrograms(load_features=True)
vid_train_set.load_resnet_features()

In [29]:
vid_test_set = vid_set(npy_file=test_list,root_dir=root_dir,lang='all',transform=transform_valid,lang_dict=langpath_train)
vid_test_set.load_waves()
vid_test_set.generate_mel_spectrograms(load_features=True)
vid_test_set.load_resnet_features()

100%|██████████| 100/100 [00:00<00:00, 111.90it/s]


In [30]:
vid_valid_set = vid_set(npy_file=valid_list,root_dir=root_dir,lang='all',transform=transform_valid,lang_dict=langpath_train)
vid_valid_set.load_waves()
vid_valid_set.generate_mel_spectrograms(load_features=True)
vid_valid_set.load_resnet_features()

100%|██████████| 100/100 [00:00<00:00, 117.06it/s]


In [31]:
params = {'batch_size': 32,
         'shuffle': True,
         'num_workers':16}

# window size

w = 16

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

In [32]:
# window size
#vid_train_set.set_window_size(w)
vid_valid_set.set_window_size(w)
vid_test_set.set_window_size(w)


In [33]:
#vid_train_set.set_window_size(w)
vid_valid_set.set_window_size(w)
vid_test_set.set_window_size(w)
#trainloader_all_v = DataLoader(vid_train_set,**params)
validloader_all_v= DataLoader(vid_valid_set,**params)
testloader_all_v= DataLoader(vid_test_set,**params)

In [34]:
import torch.nn as nn
import torch
import torchvision
def generate_vid_model():
    model = torchvision.models.video.r3d_18(pretrained=True)
    model.fc = nn.Linear(512,4,bias=True)
    criterion = nn.CrossEntropyLoss()
    optimizer = torch.optim.SGD(model.parameters(), lr=0.001, momentum=0.9)
    scheduler = torch.optim.lr_scheduler.StepLR(optimizer, 10, gamma=0.1)
    model = nn.DataParallel(model)
    
    return model, criterion, optimizer, scheduler
    

In [21]:
import copy
def train_vmod(model, criterion,optimizer,scheduler,epochs,trainloader,validloader,device):
    model.to(device)
    running_loss=0.0
    best_acc = 0

    for epoch in range(epochs):
        scheduler.step()
        for i, data in enumerate(trainloader_all_v,0):

            model.train()
            inputs = data['clip'][:, :, ::5, :, :].to(device)
            target = data['label'].to(device)
            optimizer.zero_grad()
            
            # forward + backward + optimize
            outputs = model(inputs)
            loss = criterion(outputs, target)
            loss.backward()
            optimizer.step()
            #break
            if i % 10:
                print(i)
            # print statistics
            running_loss += loss.item()
            if i % 2000 == 1999:    # print every 2000 mini-batches
                print('[%d, %5d] loss: %.3f' %
                      (epoch + 1, i + 1, running_loss / 2000))
                running_loss = 0.0
                running_loss += loss.item()

        # calculate accuracy
        with torch.no_grad():
            model.eval()
            res = torch.zeros((4,4))
            for i, data in enumerate(validloader_all_v, 0):
                # get the inputs; data is a list of [inputs, labels]
                inputs = data['clip'][:, :, ::5, :, :].to(device)
                label = data['label'].to(device)

                # forward + backward + optimize
                outputs = model(inputs)

                preds = torch.argmax(outputs,dim=1)

                for p,gt in zip(preds,label):
                    res[int(p),int(gt)] += 1


            N_total = res.sum()
            N_correct = res.diag().sum()

            acc = N_correct / N_total
            if acc > best_acc:
                print("new best acc")
                best_acc = acc
                best_model = copy.deepcopy(model) 

            print(f" Accuracy : {acc}")

    print('Finished Training')
    return best_acc,best_model


In [22]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

accs = list()
for w in [16]:
    a = list()
    vid_train_set.set_window_size(w)
    vid_valid_set.set_window_size(w)
    vid_test_set.set_window_size(w)
    
    trainloader_all_v = DataLoader(vid_train_set,**params)
    validloader_all_v= DataLoader(vid_valid_set,**params)
    testloader_all_v= DataLoader(vid_test_set,**params)
    
    model, criterion, optimizer, scheduler = generate_vid_model()
    a,best_model = train_vmod(model, criterion,optimizer,scheduler,12,trainloader_all_v,validloader_all_v,device)
    torch.save(best_model.state_dict(), "./weights/best_model_vid_"+str(w)+".pth")

1
2
3
4
5
6
7
8
9
11
12
13
14
15
16
17
18
19
21
22
23
24
25
26
27
28
29
31
32
33
34
35
36
37
38
39
41
42
43
44
45
46
47
48
49
51
52
53
54
55
56
57
58
59
61
62
63
64
65
66
67
68
69
71
72
73
74
75
76
77
78
79
81
82
83
84
85
86
87
88
89
91
92
93
94
95
96
97
98
99
101
102
103
104
105
106
107
108
109
111
112
113
114
115
116
117
118
119
121
122
123
124
125
126
127
128
129
131
132
133
134
135
136
137
138
139
141
142
143
144
145
146
147
148
149
151
152
153
154
155
156
157
158
159
161
162
163
164
165
166
167
168
169
171
172
173
174
175
176
177
178
179
181
new best acc
 Accuracy : 0.7984615564346313
1
2
3
4
5
6
7
8
9
11
12
13
14
15
16
17
18
19
21
22
23
24
25
26
27
28
29
31
32
33
34
35
36
37
38
39
41
42
43
44
45
46
47
48
49
51
52
53
54
55
56
57
58
59
61
62
63
64
65
66
67
68
69
71
72
73
74
75
76
77
78
79
81
82
83
84
85
86
87
88
89
91
92
93
94
95
96
97
98
99
101
102
103
104
105
106
107
108
109
111
112
113
114
115
116
117
118
119
121
122
123
124
125
126
127
128
129
131
132
133
134
135
136
137
138
13

In [19]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

accs = list()
for w in [8]:
    a = list()
    vid_train_set.set_window_size(w)
    vid_valid_set.set_window_size(w)
    vid_test_set.set_window_size(w)
    
    trainloader_all_v = DataLoader(vid_train_set,**params)
    validloader_all_v= DataLoader(vid_valid_set,**params)
    testloader_all_v= DataLoader(vid_test_set,**params)
    
    model, criterion, optimizer, scheduler = generate_vid_model()
    a,best_model = train_vmod(model, criterion,optimizer,scheduler,12,trainloader_all_v,validloader_all_v,device)
    torch.save(best_model.state_dict(), "./weights/best_model_vid_"+str(w)+".pth")

1
2
3
4
5
6
7
8
9
11
12
13
14
15
16
17
18
19
21
22
23
24
25
26
27
28
29
31
32
33
34
35
36
37
38
39
41
42
43
44
45
46
47
48
49
51
52
53
54
55
56
57
58
59
61
62
63
64
65
66
67
68
69
71
72
73
74
75
76
77
78
79
81
82
83
84
85
86
87
88
89
91
92
93
94
95
96
97
98
99
101
102
103
104
105
106
107
108
109
111
112
113
114
115
116
117
118
119
121
122
123
124
125
126
127
128
129
131
132
133
134
135
136
137
138
139
141
142
143
144
145
146
147
148
149
151
152
153
154
155
156
157
158
159
161
162
163
164
165
166
167
168
169
171
172
173
174
175
176
177
178
179
181
new best acc
 Accuracy : 0.8015384674072266
1
2
3
4
5
6
7
8
9
11
12
13
14
15
16
17
18
19
21
22
23
24
25
26
27
28
29
31
32
33
34
35
36
37
38
39
41
42
43
44
45
46
47
48
49
51
52
53
54
55
56
57
58
59
61
62
63
64
65
66
67
68
69
71
72
73
74
75
76
77
78
79
81
82
83
84
85
86
87
88
89
91
92
93
94
95
96
97
98
99
101
102
103
104
105
106
107
108
109
111
112
113
114
115
116
117
118
119
121
122
123
124
125
126
127
128
129
131
132
133
134
135
136
137
138
13

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

accs = list()
for w in [16]:
    a = list()
    vid_train_set.set_window_size(w)
    vid_valid_set.set_window_size(w)
    vid_test_set.set_window_size(w)
    
    trainloader_all_v = DataLoader(vid_train_set,**params)
    validloader_all_v= DataLoader(vid_valid_set,**params)
    testloader_all_v= DataLoader(vid_test_set,**params)
    
    model, criterion, optimizer, scheduler = generate_vid_model()
    a,best_model = train_vmod(model, criterion,optimizer,scheduler,12,trainloader_all_v,validloader_all_v,device)
    torch.save(best_model.state_dict(), "./weights/best_model_vid_"+str(w)+".pth")

In [17]:
best_model

NameError: name 'best_model' is not defined

In [35]:
import copy

In [70]:
def evaluate_softmax_fusion_video(dataloader,visual_model,audio_model):
    visual_model.to(device)
    audio_model.to(device)
    visual_model.eval()
    audio_model.eval()
    
    with torch.no_grad():
        res_audio = torch.zeros((4,4))
        res_visual = torch.zeros((4,4))
        res_average = torch.zeros((4,4))
        res_smax = torch.zeros((4,4))
        res_lmax = torch.zeros((4,4))
        
        all_preds = list()
        all_labels = list()
        
        for i, data in enumerate(dataloader, 0):
            # get the inputs; data is a list of [inputs, labels]
            inputs_visual = data['clip'][:, :, ::5, :, :].to(device)
            inputs_audio = data['ms_spot'].unsqueeze(1).to(device)
            label = data['label'].to(device)

            # forward + backward + optimize
            outputs_audio = audio_model(inputs_audio)
            outputs_visual = visual_model(inputs_visual)
            
            softmax_audio = torch.softmax(outputs_audio,dim=1) # MAKE SURE DIMS ARE CORRECT, TEST
            softmax_visual = torch.softmax(outputs_visual,dim=1)
            softmax_average = (softmax_audio + softmax_visual) / 2
            
            
            logit_max = torch.max(outputs_audio,outputs_visual)
            softmax_max = torch.max(softmax_audio,softmax_visual)
            
            preds_audio = torch.argmax(outputs_audio,dim=1)
            preds_visual = torch.argmax(outputs_visual,dim=1)
            preds_average = torch.argmax(softmax_average,dim=1)
            preds_smax = torch.argmax(softmax_max,dim=1)
            preds_lmax = torch.argmax(logit_max,dim=1)
            
            all_preds.append((preds_audio,preds_visual,preds_average,preds_smax,preds_lmax))
            all_labels.append(label)

            for p,gt in zip(preds_audio,label):
                res_audio[int(p),int(gt)] += 1
            
            for p,gt in zip(preds_visual,label):
                res_visual[int(p),int(gt)] += 1

            for p,gt in zip(preds_average,label):
                res_average[int(p),int(gt)] += 1
                
            for p,gt in zip(preds_smax,label):
                res_smax[int(p),int(gt)] += 1
                
            for p,gt in zip(preds_lmax,label):
                res_lmax[int(p),int(gt)] += 1
                
                
        # Audio
        N_total_audio = res_audio.sum()
        N_correct_audio = res_audio.diag().sum()
        acc_audio = N_correct_audio / N_total_audio
        
        N_total_visual = res_visual.sum()
        N_correct_visual = res_visual.diag().sum()
        acc_visual = N_correct_visual / N_total_visual
        
        N_total_average = res_average.sum()
        N_correct_average = res_average.diag().sum()
        acc_average = N_correct_average / N_total_average
        
        N_total_smax = res_smax.sum()
        N_correct_smax = res_smax.diag().sum()
        acc_smax = N_correct_smax / N_total_smax
        
        N_total_lmax = res_lmax.sum()
        N_correct_lmax = res_lmax.diag().sum()
        acc_lmax = N_correct_lmax / N_total_lmax
        
        print(f"Audio Accuracy : {acc_audio},\
              Visual Accuracy : {acc_visual},\
              Average Accuracy : {acc_average},\
              smax Accuracy : {acc_smax},\
              lmax Accuracy : {acc_lmax}")
        
        return acc_audio,acc_visual,acc_average,acc_smax,acc_lmax,(res_audio,res_visual,res_average,res_smax),(all_labels,all_preds)
    

In [74]:
avg_wv_accs_valid_16 = list()
avg_wv_accs_test_16 = list()

for w in [16]:
    vid_valid_set.set_window_size(w)
    vid_test_set.set_window_size(w)
    
    validloader = DataLoader(vid_valid_set,**params)
    testloader = DataLoader(vid_test_set,**params)
    
    # generate models
    visual_model,_,_,_ = generate_vid_model()
    audio_model, _,_ = generate_model()
    
    # load models
    visual_model.load_state_dict(torch.load("./weights/best_model_vid_"+str(w)+".pth"))
    audio_model.load_state_dict(torch.load("./weights/best_model_audio_"+str(w)+".pth"))
    
    avg_wv_accs_valid_16.append(evaluate_softmax_fusion_video(validloader,visual_model,audio_model))
    avg_wv_accs_test_16.append(evaluate_softmax_fusion_video(testloader,visual_model,audio_model))

Exception ignored in: <bound method _MultiProcessingDataLoaderIter.__del__ of <torch.utils.data.dataloader._MultiProcessingDataLoaderIter object at 0x1554cff5eda0>>
Traceback (most recent call last):
  File "/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torch/utils/data/dataloader.py", line 1203, in __del__
    self._shutdown_workers()
  File "/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torch/utils/data/dataloader.py", line 1177, in _shutdown_workers
    w.join(timeout=_utils.MP_STATUS_CHECK_INTERVAL)
  File "/usr/lib/python3.6/multiprocessing/process.py", line 122, in join
    assert self._parent_pid == os.getpid(), 'can only join a child process'
AssertionError: can only join a child process
Exception ignored in: <bound method _MultiProcessingDataLoaderIter.__del__ of <torch.utils.data.dataloader._MultiProcessingDataLoaderIter object at 0x1554cff5eda0>>
Traceback (most recent call last

    self._shutdown_workers()    self._shutdown_workers()
self._shutdown_workers()
  File "/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torch/utils/data/dataloader.py", line 1177, in _shutdown_workers

  File "/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torch/utils/data/dataloader.py", line 1177, in _shutdown_workers
Exception ignored in:       File "/home/oarongve/.local/share/virtualenvs/project-daredevil-8eBKzQn6/lib/python3.6/site-packages/torch/utils/data/dataloader.py", line 1177, in _shutdown_workers
    <bound method _MultiProcessingDataLoaderIter.__del__ of <torch.utils.data.dataloader._MultiProcessingDataLoaderIter object at 0x1554cff5eda0>>w.join(timeout=_utils.MP_STATUS_CHECK_INTERVAL)    w.join(timeout=_utils.MP_STATUS_CHECK_INTERVAL)

w.join(timeout=_utils.MP_STATUS_CHECK_INTERVAL)
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", li

Audio Accuracy : 0.7389743328094482,              Visual Accuracy : 0.908717930316925,              Average Accuracy : 0.8907692432403564,              smax Accuracy : 0.8892307877540588,              lmax Accuracy : 0.8943589925765991
Audio Accuracy : 0.7255097031593323,              Visual Accuracy : 0.8990551829338074,              Average Accuracy : 0.8906016945838928,              smax Accuracy : 0.8881153464317322,              lmax Accuracy : 0.8896071314811707


## Calculate for w = 8

In [117]:
avg_wv_accs_valid_8 = list()
avg_wv_accs_test_8 = list()

w = 8

vid_valid_set.set_window_size(w)
vid_test_set.set_window_size(w)

validloader = DataLoader(vid_valid_set,**params)
testloader = DataLoader(vid_test_set,**params)

# generate models
visual_model,_,_,_ = generate_vid_model()
audio_model, _,_ = generate_model()

# load models
visual_model.load_state_dict(torch.load("./weights/best_model_vid_"+str(w)+".pth"))
audio_model.load_state_dict(torch.load("./weights/best_model_audio_"+str(w)+".pth"))

avg_wv_accs_valid_8.append(evaluate_softmax_fusion_video(validloader,visual_model,audio_model))
avg_wv_accs_test_8.append(evaluate_softmax_fusion_video(testloader,visual_model,audio_model))

Audio Accuracy : 0.7215384840965271,              Visual Accuracy : 0.8969230651855469,              Average Accuracy : 0.8835897445678711,              smax Accuracy : 0.8789743781089783,              lmax Accuracy : 0.8589743375778198
Audio Accuracy : 0.711089015007019,              Visual Accuracy : 0.8831427097320557,              Average Accuracy : 0.877175509929657,              smax Accuracy : 0.8717055916786194,              lmax Accuracy : 0.8577821850776672


In [100]:
def get_classwise_info_vid(res,prediction_type): #hotfix
    
    # Convert type to correct index
    p_type = {
        'audio': 0,
        'visual': 1,
        'avg': 2,
        'smax': 3,
        'lmax': 4
    }
    
    # Get correct idx
    pred_idx = p_type[prediction_type]
    
    # predictoins
    y_p = list()
    for e in res[0][6][1]:
        y_p.append(e[pred_idx])
    y_p = torch.cat(y_p)
    y_p = y_p.cpu()
    
    #labels
    
    y_t = torch.cat(res[0][6][0]).cpu()
    print(sklearn.metrics.classification_report(digits=3,target_names=['Card','Substitutuion','Goal','Background'],
                                                y_true=y_t,
                                                y_pred=y_p))

In [104]:
import sklearn.metrics

In [75]:
print("Done")

Done


In [ ]:

a = 0
p_type = 1
y_p = list()
for e in avg_wv_accs_valid_16[a][5][1]:
    y_p.append(e[p_type])
y_p = torch.cat(y_p)
y_p = y_p.cpu()
l = torch.cat(avg_wv_accs_valid_16[a][5][0]).cpu()

In [ ]:
print(sklearn.metrics.classification_report(target_names=['Card','Substitutuion','Goal','Background'],y_true=l,y_pred=y_p))

In [ ]:

a = 0
p_type = 4
y_p = list()
for e in avg_wv_accs_valid_16[a][5][1]:
    y_p.append(e[p_type])
y_p = torch.cat(y_p)
y_p = y_p.cpu()
l = torch.cat(avg_wv_accs_valid_16[a][5][0]).cpu()

In [ ]:
print(sklearn.metrics.classification_report(target_names=['Card','Substitutuion','Goal','Background'],y_true=l,y_pred=y_p))

In [97]:
avg_wv_accs_valid_16[0][6][0]

[tensor([0, 3, 3, 1, 2, 2, 3, 3, 3, 3, 3, 1, 2, 1, 0, 0, 0, 2, 3, 3, 1, 0, 1, 0,
         3, 3, 1, 0, 1, 0, 1, 0], device='cuda:0'),
 tensor([3, 0, 1, 1, 1, 3, 1, 0, 2, 0, 3, 3, 2, 0, 1, 1, 0, 3, 2, 0, 0, 2, 1, 2,
         2, 3, 3, 2, 0, 2, 3, 0], device='cuda:0'),
 tensor([2, 1, 2, 3, 1, 0, 2, 1, 3, 0, 3, 0, 1, 1, 3, 0, 3, 0, 3, 1, 0, 3, 2, 0,
         1, 3, 1, 1, 3, 3, 0, 1], device='cuda:0'),
 tensor([0, 0, 2, 3, 3, 3, 3, 0, 2, 3, 1, 2, 0, 3, 1, 3, 2, 0, 3, 1, 1, 1, 1, 3,
         0, 3, 1, 3, 3, 1, 2, 3], device='cuda:0'),
 tensor([3, 3, 3, 1, 2, 0, 2, 2, 3, 1, 3, 0, 0, 1, 2, 3, 1, 1, 2, 3, 3, 3, 3, 3,
         1, 2, 2, 3, 3, 1, 3, 1], device='cuda:0'),
 tensor([0, 3, 2, 3, 3, 2, 0, 3, 1, 0, 1, 3, 1, 1, 1, 3, 1, 1, 1, 2, 0, 0, 2, 2,
         2, 3, 1, 3, 2, 1, 1, 0], device='cuda:0'),
 tensor([1, 1, 0, 2, 1, 2, 3, 3, 0, 1, 2, 3, 2, 3, 0, 3, 2, 3, 3, 1, 2, 3, 0, 1,
         2, 3, 3, 0, 1, 3, 3, 3], device='cuda:0'),
 tensor([3, 2, 1, 1, 3, 0, 3, 2, 3, 3, 1, 3, 2, 0, 3, 1, 1, 3, 2, 2, 

In [ ]:
acc_audio,acc_visual,acc_average,acc_smax,acc_lmax,(res_audio,res_visual,res_average,res_smax),(all_labels,all_preds)

# Results video

## w = 8

In [118]:
get_classwise_info_vid(avg_wv_accs_test_8, 'visual')

               precision    recall  f1-score   support

         Card      0.876     0.874     0.875       453
Substitutuion      0.925     0.870     0.897       579
         Goal      0.924     0.926     0.925       326
   Background      0.836     0.879     0.857       653

     accuracy                          0.883      2011
    macro avg      0.890     0.888     0.888      2011
 weighted avg      0.885     0.883     0.883      2011



## w = 16

In [112]:
get_classwise_info_vid(avg_wv_accs_test_16, 'visual')

               precision    recall  f1-score   support

         Card      0.900     0.874     0.887       453
Substitutuion      0.949     0.874     0.910       579
         Goal      0.913     0.966     0.939       326
   Background      0.853     0.905     0.878       653

     accuracy                          0.899      2011
    macro avg      0.904     0.905     0.904      2011
 weighted avg      0.901     0.899     0.899      2011



# Results Video + Audio

## w = 8

In [120]:
get_classwise_info_vid(avg_wv_accs_test_8, 'avg')

               precision    recall  f1-score   support

         Card      0.844     0.861     0.852       453
Substitutuion      0.894     0.877     0.886       579
         Goal      0.954     0.945     0.949       326
   Background      0.848     0.855     0.851       653

     accuracy                          0.877      2011
    macro avg      0.885     0.884     0.885      2011
 weighted avg      0.878     0.877     0.877      2011



## w = 16

In [116]:
get_classwise_info_vid(avg_wv_accs_test_16, 'avg')

               precision    recall  f1-score   support

         Card      0.868     0.868     0.868       453
Substitutuion      0.944     0.877     0.910       579
         Goal      0.954     0.960     0.957       326
   Background      0.834     0.884     0.858       653

     accuracy                          0.891      2011
    macro avg      0.900     0.897     0.898      2011
 weighted avg      0.893     0.891     0.891      2011



In [109]:
get_classwise_info_vid(avg_wv_accs_test_16, 'audio')

               precision    recall  f1-score   support

         Card      0.672     0.704     0.688       453
Substitutuion      0.777     0.674     0.722       579
         Goal      0.908     0.874     0.891       326
   Background      0.646     0.712     0.677       653

     accuracy                          0.726      2011
    macro avg      0.750     0.741     0.744      2011
 weighted avg      0.732     0.726     0.727      2011



In [69]:
avg_wv_accs_test_16[0][5][1][1]

(tensor([3, 0, 1, 1, 0, 2, 3, 0, 2, 1, 3, 3, 0, 1, 1, 1, 3, 2, 0, 2, 2, 2, 0, 0,
         3, 0, 0, 3, 3, 0, 3, 3], device='cuda:0'),
 tensor([3, 3, 1, 3, 0, 2, 0, 3, 2, 1, 3, 0, 0, 1, 1, 3, 3, 2, 1, 2, 2, 2, 0, 3,
         1, 0, 2, 3, 3, 3, 3, 3], device='cuda:0'),
 tensor([3, 3, 1, 3, 0, 2, 0, 3, 2, 1, 3, 3, 0, 1, 1, 1, 3, 2, 0, 2, 2, 2, 0, 3,
         1, 0, 2, 3, 3, 0, 3, 3], device='cuda:0'),
 tensor([3, 3, 1, 3, 0, 2, 0, 3, 2, 1, 3, 3, 0, 1, 1, 1, 3, 2, 0, 2, 2, 2, 0, 3,
         1, 0, 2, 3, 3, 3, 3, 3], device='cuda:0'),
 tensor([3, 3, 1, 3, 0, 2, 0, 3, 2, 1, 3, 3, 0, 1, 1, 1, 3, 2, 0, 2, 2, 2, 0, 3,
         3, 0, 2, 3, 3, 0, 3, 3], device='cuda:0'))

In [29]:
avg_wv_accs_valid = list()
avg_wv_accs_test = list()

for w in [8]:
    vid_valid_set.set_window_size(w)
    vid_test_set.set_window_size(w)
    
    validloader = DataLoader(vid_valid_set,**params)
    testloader = DataLoader(vid_test_set,**params)
    
    # generate models
    visual_model,_,_,_ = generate_vid_model()
    audio_model, _,_ = generate_model()
    
    # load models
    visual_model.load_state_dict(torch.load("./weights/best_model_vid_"+str(w)+".pth"))
    audio_model.load_state_dict(torch.load("./weights/best_model_audio_"+str(w)+".pth"))
    
    avg_wv_accs_valid.append(evaluate_softmax_fusion_video(validloader,visual_model,audio_model))
    avg_wv_accs_test.append(evaluate_softmax_fusion_video(testloader,visual_model,audio_model))

Audio Accuracy : 0.7215384840965271,              Visual Accuracy : 0.8969230651855469,              Average Accuracy : 0.8835897445678711,              smax Accuracy : 0.8789743781089783,              lmax Accuracy : 0.8589743375778198
Audio Accuracy : 0.711089015007019,              Visual Accuracy : 0.8831427097320557,              Average Accuracy : 0.877175509929657,              smax Accuracy : 0.8717055916786194,              lmax Accuracy : 0.8577821850776672


In [31]:
avg_wv_accs_valid

[(tensor(0.7215), tensor(0.8969), tensor(0.8836))]

In [32]:
avg_wv_accs_test

[(tensor(0.7111), tensor(0.8831), tensor(0.8772))]

In [17]:
%%bash
nvidia-smi

Wed Dec 16 01:50:53 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 418.165.02   Driver Version: 418.165.02   CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM3...  On   | 00000000:36:00.0 Off |                    0 |
| N/A   28C    P0    49W / 350W |     13MiB / 32480MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   1  Tesla V100-SXM3...  On   | 00000000:BE:00.0 Off |                    0 |
| N/A   33C    P0    49W / 350W |     13MiB / 32480MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
|   2  T

# Video - audio fusion

In [ ]:
def evaluate_softmax_fusion_video(dataloader,visual_model,audio_model):
    visual_model.to(device)
    audio_model.to(device)
    visual_model.eval()
    audio_model.eval()
    
    with torch.no_grad():
        model.eval()
        res_audio = torch.zeros((4,4))
        res_visual = torch.zeros((4,4))
        res_average = torch.zeros((4,4))
        
        for i, data in enumerate(dataloader, 0):
            # get the inputs; data is a list of [inputs, labels]
            inputs_audio = data['clip'][:, :, ::3, :, :].to(device)
            inputs_visual = data['resnet_spot'].unsqueeze(1).to(device)
            label = data['label'].to(device)

            # forward + backward + optimize
            outputs_audio = audio_model(inputs_audio)
            outputs_visual = visual_model(inputs_visual)
            
            softmax_audio = torch.softmax(outputs_audio,dim=1) # MAKE SURE DIMS ARE CORRECT, TEST
            softmax_visual = torch.softmax(outputs_visual,dim=1)
            softmax_average = (softmax_audio + softmax_visual) / 2
            
            
            
            preds_audio = torch.argmax(outputs_audio,dim=1)
            preds_visual = torch.argmax(outputs_visual,dim=1)
            preds_average = torch.argmax(softmax_average,dim=1)

            for p,gt in zip(preds_audio,label):
                res_audio[int(p),int(gt)] += 1
            
            for p,gt in zip(preds_visual,label):
                res_visual[int(p),int(gt)] += 1

            for p,gt in zip(preds_average,label):
                res_average[int(p),int(gt)] += 1
                
                
        # Audio
        N_total_audio = res_audio.sum()
        N_correct_audio = res_audio.diag().sum()
        acc_audio = N_correct_audio / N_total_audio
        
        N_total_visual = res_visual.sum()
        N_correct_visual = res_visual.diag().sum()
        acc_visual = N_correct_visual / N_total_visual
        
        N_total_average = res_average.sum()
        N_correct_average = res_average.diag().sum()
        acc_average = N_correct_average / N_total_average
        
        N_total_smax = res_smax.sum()
        N_correct_smax = res_smax.diag().sum()
        acc_smax = N_correct_smax / N_total_smax
        
        N_total_lmax = res_lmax.sum()
        N_correct_lmax = res_lmax.diag().sum()
        acc_lmax = N_correct_lmax / N_total_lmax
        
        print(f"Audio Accuracy : {acc_audio},\
              Visual Accuracy : {acc_visual},\
              Average Accuracy : {acc_average},\
              smax Accuracy : {acc_smax},\
              lmax Accuracy : {acc_lmax}")
        
        return acc_audio,acc_visual,acc_average,acc_smax,acc_lmax
    

In [ ]:
avg_w_accs_vidvalid = list()
avg_w_accs_vidtest = list()

for w in windows:
    print(w)
    valid_set_all.set_window_size(w)
    test_set_all.set_window_size(w)
    
    validloader = DataLoader(valid_set_all,**params)
    testloader = DataLoader(test_set_all,**params)
    
    # generate models
    visual_model = Net(512,w,w//2)
    audio_model, _,_ = generate_model()
    
    # load models
    visual_model.load_state_dict(torch.load("./weights/best_model_visual_"+str(w)+".pth"))
    audio_model.load_state_dict(torch.load("./weights/best_model_audio_"+str(w)+".pth"))
    
    avg_w_accs_vidvalid.append(evaluate_softmax_fusion(validloader,visual_model,audio_model))
    avg_w_accs_vidtest.append(evaluate_softmax_fusion(testloader,visual_model,audio_model))

In [ ]:
def train_model_ws_visual(model,epochs,trainloader,validloader,criterion,optimizer,scheduler,device,tensorboard_name):
    running_loss=0.0
    model.to(device)
    best_acc = 0

    writer = SummaryWriter('runs/'+tensorboard_name)

    for epoch in range(epochs):
        scheduler.step()
        for i, data in enumerate(trainloader,0):

            model.train()
            inputs = data['resnet_spot'].unsqueeze(1).to(device)
            target = data['label'].to(device)
            inputs[inputs.isnan()] = 0.0
            optimizer.zero_grad()


            # forward + backward + optimize
            outputs = model(inputs)
            loss = criterion(outputs, target)
            loss.backward()
            optimizer.step()

            # print statistics
            running_loss += loss.item()
            if i % 2000 == 1999:    # print every 2000 mini-batches
                print('[%d, %5d] loss: %.3f' %
                      (epoch + 1, i + 1, running_loss / 2000))
                running_loss = 0.0
                running_loss += loss.item()
                writer.add_scalar('training loss',
                running_loss / 2000,
                epoch * len(trainloader) + i)
                # print statistics


        # calculate accuracy
        with torch.no_grad():
            model.eval()
            res = torch.zeros((4,4))
            for i, data in enumerate(validloader, 0):
                # get the inputs; data is a list of [inputs, labels]
                inputs = data['resnet_spot'].unsqueeze(1).to(device)
                label = data['label'].to(device)

                # forward + backward + optimize
                outputs = model(inputs)

                preds = torch.argmax(outputs,dim=1)

                for p,gt in zip(preds,label):
                    res[int(p),int(gt)] += 1




            N_total = res.sum()
            N_correct = res.diag().sum()

            acc = N_correct / N_total
            if acc > best_acc:
                print("new best acc")
                best_acc = acc
                best_model = copy.deepcopy(model) 

            writer.add_scalar('accuracy validation',
                acc,
                epoch * len(validloader) + i)
            print(f" Accuracy : {acc}")
        
    print('Finished Training')
    return best_model,best_acc